In [1]:
%%javascript
var width = window.innerWidth || document.documentElement.clientWidth || document.body.clientWidth;
var height = window.innerHeight || document.documentElement.clientHeight || document.body.clientHeight;

IPython.notebook.kernel.execute("windowSize = (" + width + "," + height + ")");
// suitable for small screens
nbpresent.mode.tree.set(
    ["app", "theme-manager", "themes", "my-theme"], 
    {
    palette: {
        "blue": { id: "blue", rgb: [0, 153, 204] },
        "black": { id: "black", rgb: [0, 0, 0] },
        "white": { id: "white", rgb: [255, 255, 255] },
        "red": { id: "red", rgb: [240, 32, 32] },
        "gray": { id: "gray", rgb: [128, 128, 128] },
    },
    backgrounds: {
        "my-background": {
            "background-color": "white"
        }
    },
    "text-base": {
        "font-family": "Georgia",
        "font-size": 2.5
    },
    rules: {
        h1: {
            "font-size": 5.5,
            color: "blue",
            "text-align": "center"
        },
        h2: {
            "font-size": 3,
            color: "blue",
            "text-align": "center"
        },
        h3: {
            "font-size": 3,
            color: "black",
        },
        "ul li": {
            "font-size": 2.5,
            color: "black"
        },
        "ul li ul li": {
            "font-size": 2.0,
            color: "black"
        },
        "code": {
            "font-size": 1.6,
        },
        "pre": {
            "font-size": 1.6,
        }
    }
});

<IPython.core.display.Javascript object>

# Advanced Sequence Alignment

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Clustal.png" width="800" class="centerImg">

* Problem Set #4 is posted.

<p style="text-align: right; clear: right;">1</p>

# Recall Local Alignment


<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalRecurrence.png" width="600" class="centerImg">

* The *zero* is our *free ride* that allows the node to restart with a score of 0 at any point
  - What does this imply?
* After solving for the entire score matrix, we then search for s<sub>i,j</sub> with the highest score, this is $(i_2,j_2)$
* We follow our back tracking matrix until we reach a *score* of 0, whose coordinate becomes $(i_1,j_1)$

<p style="text-align: right; clear: right;">2</p>

# Smith-Waterman Local Alignment

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/SmithWaterman.png" width="600" class="centerImg">

**Key idea:** Adding *"free-rides"* from the source to any intersection

<p style="text-align: right; clear: right;">3</p>

# A Local Alignment Example

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample01.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">4</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample02.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">5</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample03.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">6</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample04.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">7</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample05.png" width="800" class="centerImg">

* Once the matrix is filled in we find the best alignment
* Rather than using the score of the last entry as we did for a global alignment,<br> we search for the entire matrix for the maximum entry (*O(m n)* steps)

<p style="text-align: right; clear: right;">8</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample06.png" width="600" class="centerImg">

* From the largest score attained, then backtrack from there until a beginning "0" is reached to find the alignment.

<p style="text-align: right; clear: right;">9</p>

# A Local Alignment Example - continued

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/LocalExample07.png" width="600" class="centerImg">

<p style="text-align: right; clear: right;">10</p>

In [3]:
import numpy

def LocalAlign(v, w, scorematrix, indel):
    s = numpy.zeros((len(v)+1,len(w)+1), dtype="int32")
    b = numpy.zeros((len(v)+1,len(w)+1), dtype="int32")
    for i in xrange(1,len(v)+1):
        for j in xrange(1,len(w)+1):
            if (j == 0):
                if (i > 0):
                    s[i,j] = max(s[i-1,j] + indel, 0)
                    b[i,j] = 1
                continue
            if (i == 0):
                s[i,j] = max(s[i,j-1] + indel, 0)
                b[i,j] = 2
                continue
            score = s[i-1,j-1] + scorematrix[v[i-1],w[j-1]]
            vskip = s[i-1,j] + indel
            wskip = s[i,j-1] + indel
            s[i,j] = max(vskip, wskip, score, 0)
            if (s[i,j] == vskip):
                b[i,j] = 1
            elif (s[i,j] == wskip):
                b[i,j] = 2
            elif (s[i,j] == score):
                b[i,j] = 3
            else:
                b[i,j] = 0
    return (s, b)

match = {('A','A'):  5, ('A','C'): -4, ('A','G'): -4, ('A','T'): -4,
         ('C','A'): -4, ('C','C'):  5, ('C','G'): -4, ('C','T'): -4,
         ('G','A'): -4, ('G','C'): -4, ('G','G'):  5, ('G','T'): -4,
         ('T','A'): -4, ('T','C'): -4, ('T','G'): -4, ('T','T'):  5}

v = "GCTGGAAGGCAT"
w = "GCAGAGCACT"

s, b = LocalAlign(v,w,match,-7)
print s
print
print b

[[ 0  0  0  0  0  0  0  0  0  0  0]
 [ 0  5  0  0  5  0  5  0  0  0  0]
 [ 0  0 10  3  0  1  0 10  3  5  0]
 [ 0  0  3  6  0  0  0  3  6  0 10]
 [ 0  5  0  0 11  4  5  0  0  2  3]
 [ 0  5  1  0  5  7  9  2  0  0  0]
 [ 0  0  1  6  0 10  3  5  7  0  0]
 [ 0  0  0  6  2  5  6  0 10  3  0]
 [ 0  5  0  0 11  4 10  3  3  6  0]
 [ 0  5  1  0  5  7  9  6  0  0  2]
 [ 0  0 10  3  0  1  3 14  7  5  0]
 [ 0  0  3 15  8  5  0  7 19 12  5]
 [ 0  0  0  8 11  4  1  0 12 15 17]]

[[0 0 0 0 0 0 0 0 0 0 0]
 [0 3 0 0 3 0 3 0 0 0 0]
 [0 0 3 2 0 3 0 3 2 3 0]
 [0 0 1 3 0 0 0 1 3 0 3]
 [0 3 0 0 3 2 3 0 0 3 1]
 [0 3 3 0 3 3 3 2 0 0 0]
 [0 0 3 3 0 3 2 3 3 2 0]
 [0 0 0 3 3 3 3 0 3 2 0]
 [0 3 0 0 3 2 3 2 1 3 0]
 [0 3 3 0 3 3 3 3 0 0 3]
 [0 0 3 2 0 3 3 3 2 3 0]
 [0 0 1 3 2 3 0 1 3 2 2]
 [0 0 0 1 3 2 3 1 1 3 3]]


# Scoring Indels: Naive Approach

<pre style="font-size: 100%;">
            ATCTTCAGCCATAAAAGATGAAGTT        Reference
            ATCTTCAGCCAAAGATGAAGTT           3 base deletion relative to the reference<br>
            ATCTTCAGCC<span style="background: red;">---</span>AAAGATGAAGTT        version 1
            ATCTTCAGCCA<span style="background: red;">---</span>AAGATGAAGTT        version 2
            ATCTTCAGCCA<span style="background: red;">--</span>A<span style="background: red;">-</span>AGATGAAGTT        version 3
            ATCTTCAGCCA<span style="background: red;">-</span>AA<span style="background: red;">--</span>GATGAAGTT        version 4
            ATCTTCAGCCA<span style="background: red;">-</span>A<span style="background: red;">-</span>A<span style="background: red;">-</span>GATGAAGTT        version 5<br>
            ATCTTCAGCCATA<span style="background: green;">TGTG</span>AAAGATGAAGTT    4 base insertion
</pre>
* A fixed penalty σ is given to every indel:
  - -σ for 1 indel, 
  - -2σ for 2 consecutive  indels
  - -3σ for 3 consecutive  indels, etc.

* Can be too severe penalty for a series of 100 consecutive indels
  - large insertions or deletions might result from a single event

<p style="text-align: right; clear: right;">11</p>

# Affine Gap Penalties

* In nature, a series of *k* indels often come as a single event rather than a series of *k* single nucleotide events:
<br><br>
<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AffineGapPenalties.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">12</p>

# Accounting for Gaps

* Gaps- contiguous sequence of indels in one of the rows

* Modify the scoring for a gap of length x to be:

 <span style="font-size: 150%; margin-left: 550px;">-(&rho; + &sigma;x)</span>

    where &rho;+&sigma; > 0 is the penalty for introducing a gap:
    
    <p style="color: red;text-align: center;">&rho; = gap opening penalty</p>
                      
    and σ is the cost of extending it further (ρ+σ >>σ):
    
    <p style="color: red;text-align: center;">&sigma; = gap extension penalty</p>

    because you do not want to add too much of a penalty for further extending the gap, once it is opened.

<p style="text-align: right; clear: right;">13</p>

# Affine Gap Penalties

Gap penalties:
<ul style="font-size: 150%;">
    <li>-ρ - σ  when there is 1 indel</li>
    <li>-ρ - 2σ  when there are 2 indels</li>
    <li>-ρ - 3σ  when there are 3 indels, etc.</li> 
    <li>-ρ - x·σ (-gap opening - x gap extensions)</li>
</ul>

Somehow reduced penalties (as compared to naïve scoring) are given to runs of horizontal and vertical edges

<p style="text-align: right; clear: right;">14</p>

# Adding Affine Gap Penalties to our Graph

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AffineGraph.png" width="400" style="float: right;">

* To reflect affine gap penalties we have to add “long” horizontal and vertical edges to the edit graph.

* Each such edge of length x should have weight -ρ - x·σ

* There are many such edges!

* Adding them to the graph increases the running time of the alignment algorithm by a factor of n (where n is the number of vertices)

* So the complexity increases from $O(n^2)$ to $O(n^3)$

<p style="text-align: right; clear: right;">15</p>

# Adding Two More Tables

* Affine Gap penalties can be more easily expressed in terms of 3 recurrences

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AffineGapRecurrences.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">16</p>

# A 3-level Manhattan Grid

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Manhattan3Level.png" width="600" class="centerImg">


* The three recurrences for the scoring algorithm creates a 3-layered graph. 
* The top level creates/extends gaps in the sequence *w*.  
* The bottom level creates/extends gaps in sequence *v*. 
* The middle level extends matches and mismatches.

<p style="text-align: right; clear: right;">17</p>

# Switching between 3 Layers

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Manhattan3Layer.png" width="500" class="centerImg">

* Levels:
  - The main level is for diagonal edges  
  - The lower level is for horizontal edges
  - The upper level is for vertical edges
  
* A jumping penalty is assigned to moving from the main level to either the upper level or the lower level (-ρ - σ)

* There is a gap extension penalty for each continuation on a level other than the main level (-σ)

<p style="text-align: right; clear: right;">18</p>

# Multiple Alignment versus Pairwise Alignment

<table style="float: right; margin-left: 50px;"><tbody>
<tr><td><img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/MWaterman.jpg"></td><td><img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Cat.jpg"></td></tr>
<tr><td><img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Dog.jpg"></td><td><img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Pig.jpg"></td></tr>
</tbody></table>

* Up until now we have only tried to align two sequences. 
* What about more than two?  And what for? 
* A faint similarity between two sequences becomes significant if present in many
* Multiple alignments can reveal subtle similarities that pairwise alignments do not reveal


<p style="text-align: right; clear: right;">19</p>

# Generalizing Pairwise Alignment

* Alignment of 2 sequences is represented as a 2-row matrix
* In a similar way, we represent alignment of 3 sequences as a 3-row matrix 

<pre style="font-size: 120%;">
          A T _ G C G _
          A _ C G T _ A
          A T C A C _ A
</pre>

* Score: more conserved columns, better alignment

<p style="text-align: right; clear: right;">20</p>

# Three-D Alignment Paths

* An alignment of 3 sequences: ATGC, AATC, ATGC

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AlignThree.png" width="600" class="centerImg">

* Resulting path in (x,y,z) space:<br>
    (0,0,0) &rarr; (1,1,0) &rarr; (1,2,1) &rarr; (2,3,2) &rarr; (3,3,3) &rarr; (4,4,4)
* Is there a better one?

<p style="text-align: right; clear: right;">21</p>

# Aligning Three Sequences

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AlignmentCube.png" width="400" class="centerImg">

* Same strategy as aligning two sequences
* Use a 3-D “Manhattan Cube”, with each axis representing a sequence to align
* For global alignments, go from source to sink

<p style="text-align: right; clear: right;">22</p>

# 2-sequence vs 3-sequence Alignment

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/EditGraphs2D3D.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">23</p>

# A 2-D cell versus a 3-D Alignment Cell

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AlignmentEdges.png" width="600" class="centerImg">

* 2-D *[(i-1,j-1), (i-1,j), (i,j-1)] &rarr; (i,j)* (3 directions)
* 3-D *[(i-1,j-1,k-1), (i-1,j,k), (i,j-1,k), (i,j,k-1), (i,j-1,k-1), (i-1,j,k-1), (i-1,j-1,k),] &rarr; (i,j,k)*  (7 directions)
* N-D (2<sup>N</sup> -1 directions)

<p style="text-align: right; clear: right;">24</p>

# Structure of a 3-D Alignment Cell

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/AlignmentPaths.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">25</p>

# Multiple Alignment: Recursion Relation

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/Align3Recursion.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">26</p>

# Multiple Alignment: Running Time

* For 3 sequences of length n, the run time is $7n^3$; $O(n^3)$

* For k sequences, build a k-dimensional Manhattan, with run time $(2^k-1)(n^k)$; $O(2^kn^k)$

* Conclusion: dynamic programming approach for alignment between two sequences is easily extended to k sequences but it is impractical due to exponential running time

<p style="text-align: right; clear: right;">27</p>

# Multiple Alignment Induces Pairwise Alignments

Every multiple alignment induces pairwise alignments
<pre style="font-size: 120%;">		
			  x:	AC-GCGG-C		
			  y:	AC-GC-GAG
			  z:	GCCGC-GAG
</pre>
Induces:
<pre style="font-size: 120%;">		
        x: ACGCGG-C;  x: AC-GCGG-C;  y: AC-GCGAG
        y: ACGC-GAC;  z: GCCGC-GAG;  z: GCCGCGAG
</pre>
<p style="text-align: right; clear: right;">28</p>

# Inverse Problem

Do Pairwise Alignments imply a Multiple Alignment?

* Given 3 arbitrary pairwise alignments: 
<pre style="font-size: 120%;">
        x: ACGCTGG-C;  x: AC-GCTGG-C;  y: AC-GC-GAG
        y: ACGC--GAC;  z: GCCGCA-GAG;  z: GCCGCAGAG
</pre>
  
* Can we construct a multiple alignment that induces  them?     
         
<p style="text-align: center; font-size: 120%;">NOT ALWAYS</p>

* Why? Because pairwise alignments may be arbitrarily inconsistent

<p style="text-align: right; clear: right;">29</p>

# Combining Optimal Pairwise Alignments 

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/MultipleFromPairs.png" width="500" style="float: right;">

* In some cases we can combine pairwie alignments into a single multiple alignment
* But, in others we cannot because one alignment makes a choice that is inconsistent with the overall best choice
<pre style="font-size: 100%;">
 AAAATTTT--------          ----AAAATTTT----
 ----TTTTGGGG----   -OR-   --------TTTTGGGG
 --------GGGGAAAA          GGGGAAAA--------
</pre>
* Is there another way?

<p style="text-align: right; clear: right;">30</p>

# Multiple Alignment from Pairwise Alignments

* From an optimal multiple alignment, we can infer pairwise alignments between all pairs of sequences, but they are not necessarily optimal
* It is difficult to infer a “good” multiple alignment from optimal pairwise alignments between all sequences
* Are we stuck, or is there some other trick?

<p style="text-align: right; clear: right;">31</p>

# Multiple Alignment using a Profile Scores

* We used profile scores earlier when we discussed Motif finding
<pre style="font-size: 100%;">
              -  A  G  G  C  T  A  T  C  A  C  C  T  G 
              T  A  G  –  C  T  A  C  C  A  -  -  -  G 
              C  A  G  –  C  T  A  C  C  A  -  -  -  G 
              C  A  G  –  C  T  A  T  C  A  C  –  G  G 
              C  A  G  –  C  T  A  T  C  G  C  –  G  G 

        A	 0  5  0  0  0  0  5  0  0  4  0  0  0  0    
        C	 3  0  0  0  5  0  0  2  5  0  3  1  0  0
        G	 0  0  5  1  0  0  0  0  0  1  0  0  2  5
        T	 1  0  0  0  0  5  0  3  0  0  0  0  1  0
        -	 1  0  0  4  0  0  0  0  0  0  2  4  2  0
</pre>
* Thus far we have aligned sequences against other sequences

* Can we align a sequence against a profile? 

* Can we align a profile against a profile? 

<p style="text-align: right; clear: right;">32</p>

# Aligning Alignments

A more general version of the multi-alignment problem:

* Given two alignments, can we align them? 
<pre style="font-size: 100%;">
        x: GGGCACTGCAT
        y: GGTTACGTC--    Alignment 1 
        z: GGGAACTGCAG

        w: GGACGTACC--    Alignment 2
        v: GGACCT-----
</pre>

* Idea: don’t use the sequences, but align their profiles

<pre style="font-size: 100%;">
        x: GGGCAC=TGCAT
        y: GGTTAC=GTC-- 
        z: GGGAAC=TGCAG     Combined Alignment
           ||  || | |
        w: GG==ACGTACC--    
        v: GG==ACCT-----
</pre>
<p style="text-align: right; clear: right;">33</p>

# Profile-Based Multiple Alignment: A Greedy Approach

* Choose the most similar pair of strings and combine them into a profile, thereby reducing alignment of *k* sequences to an alignment of of *k-1* sequences/profiles. **Repeat**
* This is a heuristic *greedy* method

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/ProfileAlign.png" width="800" class="centerImg">

<p style="text-align: right; clear: right;">34</p>

# Example

* Consider these 4 sequences

<pre style="font-size: 150%;">

    s<sub>1</sub>:	GATTCA
    s<sub>2</sub>:	GTCTGA
    s<sub>3</sub>:	GATATT
    s<sub>4</sub>:	GTCAGC

</pre>

* with the scoring matrix: {Match = 1, Mismatch = -1, Indel = -1}

<p style="text-align: right; clear: right;">35</p>

# Example (continued)

* There are ${4 \choose 2} = 6$ possible pairwise alignments

<pre style="font-size: 100%;">

    s<sub>2</sub>:  GTCTGA                          s<sub>1</sub>:  GATTCA--
    s<sub>4</sub>:  GTCAGC (score = 2)              s<sub>4</sub>:  G-T-CAGC (score = 0)

    s<sub>1</sub>:  GAT-TCA                         s<sub>2</sub>:  G-TCTGA
    s<sub>2</sub>:  G-TCTGA (score = 1)             s<sub>3</sub>:  GATAT-T (score  = -1)

    s<sub>1</sub>:  GAT-TCA                         s<sub>3</sub>:  GAT-ATT
    s<sub>3</sub>:  GATAT-T (score  = 1)            s<sub>4</sub>:  G-TCAGC (score = -1)

</pre>

* The best pairwise score, 2, is between s<sub>2</sub> and s<sub>4</sub>

<p style="text-align: right; clear: right;">36</p>

# Example (continued)

* Combine s<sub>2</sub> and s<sub>4</sub>:
<pre style="font-size: 80%;">
      s<sub>2</sub>:  G T C T G A
           | | |   |         &rarr;      s<sub>2,4</sub>:  G T C t/a G a/c
      s<sub>4</sub>:  G T C A G C
</pre>
* Giving a set of three sequences:
<pre style="font-size: 80%;">
    s<sub>1  </sub>:	G  A  T  T  C  A
    s<sub>3  </sub>:	G  A  T  A  T  T
    s<sub>2,4</sub>:    G  T  C t/a G a/c
</pre>

* **Repeat** for ${3 \choose 2} = 3$ possible pairwise alignments
<pre style="font-size: 80%;">
    s<sub>1  </sub>:  GAT-TCA
    s<sub>3  </sub>:  GATAT-T (score  = 1 + 1 + 1 - 1 + 1 - 1 - 1 = 1)

    s<sub>1  </sub>:  GAT-TCA
    s<sub>2,4</sub>:  G-TCtGa (score  = 2 - 2 + 2 - 2 + &half; - 1 + &half; = 0)

    s<sub>3  </sub>:  GATAT-T
    s<sub>2,4</sub>:  G-TCtGa (score  = 2 - 2 + 2 - 2 + &half; - 1 - 1 = -1&half;)
</pre>

<p style="text-align: right; clear: right;">37</p>

# Progressive Alignment

* Progressive alignment is a variation of a greedy profile alignment algorithm with a somewhat more intelligent strategy for choosing the order of alignments.

* Progressive alignment works well for close sequences, but deteriorates for distant sequences
  * Once a gap appears in a consensus string it is permanent
  * Uses profiles to compare sequences

* CLUSTAL OMEGA

<p style="text-align: right; clear: right;">38</p>

# Clustal Omega

* A popular multiple alignment tool commonly used today
* ‘W’ stands for ‘weighted’ (different parts of alignment are weighted differently).

* Three-step process
  1. Construct pairwise alignments
  2. Build Guide Tree
  3. Progressive Alignment guided by the tree

<p style="text-align: right; clear: right;">39</p>

# Clustal Omega's First Step

Pairwise alignment

* Align each sequence against all others giving a similarity matrix
* Similarity = exact matches / sequence length (percent identity)


<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/ClustalWStep1.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">40</p>

# ClustalW's Second Step

* Create Guide Tree using the similarity matrix
  - ClustalW uses the neighbor-joining method<br>(we will discuss tre construction and clustering later in the course)
  - Guide tree roughly reflects evolutionary relations

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/ClustalWStep2.png" width="700" class="centerImg">

<p style="text-align: right; clear: right;">41</p>

# ClustalW's Third Step

* Start by aligning the two most similar sequences
* Following the guide tree, add in the next sequences, aligning to the existing alignment
* Insert gaps as necessary

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/ClustalWStep3.png" width="900" class="centerImg">

<p style="text-align: right; clear: right;">42</p>

# Next Time

<img src="http://csbio.unc.edu/mcmillan/Comp555S18/Media/DPCartoon.png" width="500" style="float: right; margin-right: 100px;">
<ul style="font-size: 24px; line-height: 32px;">
<li>Other Dynamic Programming problems</li>
<li>Divide-and-Conquer</li>
<li>Other approaches to sequence alignment</li>
</ul>

<p style="text-align: right; clear: right;">43</p>